In [1]:
import folium
import requests
import json
import geopandas as gpd
from pprint import pprint

In [2]:
stations = gpd.read_file('./data/Dublin_Ireland/Garda_Stations_-_An_Garda_Siochana/fd2555c3-3ac8-4175-aef8-b1a58cb5e20a2020314-1-1wrinib.wi1s.shp')
districts = gpd.read_file('./data/Dublin_Ireland/Dublin_census_electoral_division_2022.shp')

In [3]:
districts.columns, stations.columns

(Index(['GUID', 'GEOGID', 'GEOGDESC', 'Reference_', 'ED_GUID', 'ED_ID_STR',
        'ED_ENGLISH', 'ED_GAEILGE', 'ED_OFFICIA', 'LEA_GUID', 'CSO_LEA',
        'LEA_ID', 'LEA_OFFICI', 'LA_GUID', 'LOCAL_AUTH', 'LA_CODE', 'COUNTY',
        'CONTAE', 'PROVINCE', 'NUTS3', 'NUTS3_NAME', 'NUTS2', 'NUTS2_NAME',
        'NUTS1', 'NUTS1_NAME', 'T1_1AGETF_', 'T1_1AGETM_', 'T1_1AGETT_',
        'T6_8_O_Nor', 'T6_8_TA_No', 'T6_8_UHH_N', 'T6_8_OVD_N', 'T6_8_T_Nor',
        'AREA', 'AREA_UOM', 'GUID_17010', 'T1_2SGLM', 'T1_2MARM', 'T1_2SEPM',
        'T1_2DIVM', 'T1_2WIDM', 'T1_2TM', 'T1_2SGLF', 'T1_2MARF', 'T1_2SEPF',
        'T1_2DIVF', 'T1_2WIDF', 'T1_2TF', 'T1_2SGLT', 'T1_2MART', 'T1_2SEPT',
        'T1_2DIVT', 'T1_2WIDT', 'T1_2T', 'geometry'],
       dtype='object'),
 Index(['FID', 'STATION_NA', 'DIVISION_H', 'STN_CODE', 'ADDRESS', 'COUNTY',
        'STATION_IN', 'IG_EAST', 'IG_NORTH', 'ITM_EAST', 'ITM_NORTH',
        'LONGITUDE', 'LATITUDE', 'FULL_TIME_', 'AREA_CODE', 'PHONE_NUMB',
        'STATI

In [4]:
districts['pop_dens'] = districts['T1_2T'] / districts['AREA']

In [5]:
districts.to_crs(4326, inplace=True)
stations.to_crs(4326, inplace=True)

In [15]:
map = folium.Map(location=[53.350140, -6.266155], zoom_start=11, tiles='CartoDB Positron')
# folium.GeoJson(json.loads(result['isochrones'])).add_to(map)
folium.Choropleth(
    geo_data=districts['geometry'],  
    data=districts['pop_dens'], 
    columns=['geometry', 'pop_dens'], 
    key_on='feature.id', 
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.2, 
    legend_name="Population Density"
).add_to(map)
# folium.GeoJson(stations).add_to(map)
map

In [7]:
filtered_dists = districts.sort_values(by='pop_dens', ascending=False)[0:40]
filtered_stations = stations.clip(filtered_dists)

In [14]:
map = folium.Map(location=[53.350140, -6.266155], zoom_start=11, tiles='CartoDB Positron')
# folium.GeoJson(json.loads(result['isochrones'])).add_to(map)
folium.Choropleth(
    geo_data=filtered_dists['geometry'],  
    data=filtered_dists['pop_dens'], 
    columns=['geometry', 'pop_dens'], 
    key_on='feature.id', 
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.2, 
    legend_name="Population Density"
).add_to(map)
folium.GeoJson(filtered_stations).add_to(map)
bounds = filtered_dists.total_bounds
map.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])
map

In [9]:
filtered_center_points = list(zip(*[filtered_stations.geometry.y, filtered_stations.geometry.x]))
filtered_center_points

[(53.321316610260546, -6.2670037253805955),
 (53.338981791948015, -6.270247951311799),
 (53.34708024771032, -6.274129827967963),
 (53.35045541508416, -6.252246157372237),
 (53.35773544464533, -6.25535918655942),
 (53.36048422342, -6.266824799341576)]

In [10]:
# url = 'http://localhost:8086/isomap'
url = 'http://135.234.212.65:8086/isomap'
data = {
    'center_points': filtered_center_points, 
    'networktype': 'walk', 
    'travel_time': 15
}
payload = {
    "data": data, 
    "speeds": {
        "walk": 4500,
        "bike": 18000,
        "drive": 60000
    }
}

In [11]:
response = requests.post(url, json=payload)
if response.status_code == 200: 
    print("Request was successful. ")
    result = response.json()
else: 
    print(f"Failed to retreive response. Response message: {response.status_code}")

Request was successful. 


In [16]:
map = folium.Map(location=[53.350140, -6.266155], zoom_start=13, tiles='CartoDB Positron')
folium.Choropleth(
    geo_data=districts['geometry'],  
    data=districts['pop_dens'], 
    columns=['geometry', 'pop_dens'], 
    key_on='feature.id', 
    fill_color='YlGnBu', 
    fill_opacity=0.7, 
    line_opacity=0.2, 
    legend_name="Population Density"
).add_to(map)
# isomap = json.loads(result['isochrones'])
folium.GeoJson(filtered_dists, 
              style_function=lambda feature: {
                  'fillColor': 'white', 
                  'color': 'black', 
                  'weight': 1.5,
                  'fillOpacity': 0
              }).add_to(map)
isomap = gpd.read_file(result['isochrones'])
folium.GeoJson(isomap).add_to(map)
folium.GeoJson(filtered_stations).add_to(map)
bounds = isomap.total_bounds
map.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])
map

In [18]:
isomap.to_file('./results/isomap_garda_stations_40_ED_highest_popdens_Dublin_Ireland.shp')
map.save('./results/isomap_garda_stations_40_ED_highest_popdens_Dublin_Ireland.html')